In [1]:
from bs4 import BeautifulSoup, NavigableString, Tag
import ebooklib
from ebooklib import epub
import os
import re
from typing import Generator, List

def parse_ebook_html(ebook_path: str, try_chapter : bool = False) -> Generator[tuple, None, None]:
    """
    Parses the HTML content of an EPUB file, yielding only text content from each <p> block,
    while skipping specific elements with class 'calibre3' but considering valid text that follows.

    Parameters:
    - ebook_path (str): The path to the EPUB file.
    - try_chapter (bool): If True, the first paragraph of each chapter will be used to determine the chapter title.

    Returns:
    - text_generator (Generator[tuple, None, None]): A generator yielding text content.
    """
    book = epub.read_epub(ebook_path)
    basename = os.path.basename(ebook_path)
    noext = os.path.splitext(basename)[0]
    chapter_idx = 0
    paragraph_idx = 0
    cumsum_char_count = 0
    for item in book.get_items_of_type(ebooklib.ITEM_DOCUMENT):
        content = item.get_content().decode('utf-8')
        results = list(html_tokenizer(content, try_chapter))
        if len(results) == 0:
            continue
        chapter_idx += 1
        for row in results:
            if len(row[1]) == 0:
                continue
            paragraph_idx += 1
            char_count = len((row[1]))
            cumsum_char_count += char_count
            row = [noext, paragraph_idx, chapter_idx] + list(row[:]) + [char_count, cumsum_char_count]
            yield tuple(row)

def html_tokenizer(html_content: str, try_chapter) -> Generator[tuple, None, None]:
    """
    Generator function to tokenize HTML content, yielding text content from each <p> block.

    Parameters:
    - html_content (str): The HTML content to be tokenized.
    - try_chapter (bool): If True, the first paragraph of each chapter will be used to determine the chapter title.

    Yields:
    - text_generator (Generator[tuple, None, None]): A generator yielding text content. 
    """
    soup = BeautifulSoup(html_content, 'html.parser')
    fix_quote = re.compile(r'“|”|»|«')
    fix_threedot = re.compile(r'…')
    fix_bars = re.compile(r'\|\s*\|')

    def extract_and_yield_text(element, accumulated_texts: List[str]):
        if isinstance(element, NavigableString):
            accumulated_texts.append(str(element))
        elif isinstance(element, Tag):
            if element.name == 'a' and 'calibre3' in element.get('class', []):
                # Skip processing the <a class="calibre3"> tag itself, but not its siblings
                #print('skipping', element)
                return
            if element.name == 'span' and 'italic' in element.get('class', []):
                # Append italic text directly to the accumulated_texts list without yielding
                accumulated_texts.append(element.get_text())
            else:
                # Recursively process all children, including those following skipped elements
                for child in element.children:
                    extract_and_yield_text(child, accumulated_texts)

    chapter = None
    for i, p_tag in enumerate(soup.find_all('p')):
        accumulated_texts = []
        # if p's class is calibre14, skip it because it's metadata
        if 'calibre14' in p_tag.get('class', []):
            #print('skipping', i)
            #continue
            pass
        else:
            #print('processing', i)
            if i == 0 and try_chapter:
                # Instead of processing, this contains our chapter and title
                markers = []
                for span in p_tag.find_all('span', class_='bold'):
                    markers.append(span.get_text())

                if len(markers) >= 2:
                    chapter = ' '.join(markers)
                continue
                    
        extract_and_yield_text(p_tag, accumulated_texts)
        # if our text is '| |', skip it
        if '| |' in ' '.join(accumulated_texts):
            continue
        text = ' '.join([text.strip() for text in accumulated_texts if text.strip()])
        text = text.replace(u'\xa0', u' ')
        text = fix_quote.sub(u'"', text)
        text = fix_threedot.sub(u'...', text)
        text = fix_bars.sub(u'', text)
        text = text.strip()
        # If the first character is a capital letter, then a space, followed by more capital letters, it is likely the beginning of a chapter and needs to have the space removed
        if len(text) == 0:
            continue
        elif len(text) > 2 and text[0].isupper() and text[1] == ' ' and text[2].isupper():
            text = text[0] + text[2:]
        yield chapter, text


In [2]:
from glob import glob
import pandas as pd

# special rules.
# cryptonomicon requires try_chapter=True, and needs '| |' removed
special = {
    'cryptonomicon': {'try_chapter': True, 'clip': [(1,2),], 'drop': [106]},
    'neuromancer' : {'clip': [(1,49)], 'drop': [28]},
    'burningchrome' : { "try_chapter": True, 'drop': [1]},
    'snowcrash'     : { "try_chapter": True, 'drop': [74, 75, 76, 77], 'clip': [(1, 80), (4590, 4636)]},
    'quicksilver' : {},
    'monalisa' : {'clip': [(2969, 2984)], 'drop': [6]},
    'theconfusion' : {},
    'systemofworld' : {'clip': [(261, 331)]},
    'forwearemany': {'try_chapter': True, 'drop': [1,2,3,4,5,6, 84, 85, 86]},
    'allsystemsred': {'drop': [1,2,11,12,13,14,15]},
    'artificialcondition': {'try_chapter': True, 'drop': [1,2,12,13,14,15,16]},
    'rogueprotocol': {'drop': [1,2,10,11,12,13]},
    'exitstrategy': {'try_chapter': True, 'drop': [1,2,11,12,13,14,15]},
    'networkeffect': {'drop': [1,2,24,25,26,27,28]},   
    'fugitivetelemetry': {'drop': [1,2,11,12,13,14]},
    'systemcollapse': {'drop': [1,2,16,17,18,19]},
    'alteredcarbon': {'drop': [1,2,3,4,5]},
    'readyplayerone': {'drop': [1,2,3,4, 48, 49]},
    'gnomon': {'drop': [1,2,3,4,5,34,35,36]},
    'themoonisaharshmistress': {'drop': [1,2,3,4]},
    'cantileforleibowitz': {'drop': [1,2,3,4,37,38]},
    '1984': {'drop': [1,2,3,4,5]},
    '2xs': {'drop': [1,2,32], 'try_chapter': True},
    'agency': {'drop': [1,112,113,114,115,116]},
    'all_these_worlds': {'drop': [1,2,3,4,5,6,7], 'try_chapter': True},
    'all_tomorrows_parties': {'drop': [1,2,3,4]},
    'beyond_the_pale': {'drop': [1,2,3,4,5,59,60,61], 'try_chapter': True},
    'black_madonna': {'drop': [1,2,33], 'try_chapter': True},
    'blood_sport': {'drop': [1,2,3,4,33,34], 'try_chapter': True},
    'brave_new_world': {'drop': [1,2,3], 'try_chapter': True},
    'burning_bright': {'drop': [1], 'try_chapter': True},
    'changeling': {},
    'choose_your_enemies_carefully': {'drop': [1,2,3,4,51,52], 'try_chapter': True},
    'clockwork_asylum': {'drop': [1,2,3,50,51], 'try_chapter': True},
    'dead_air': {'drop': [1,2,3,4,5,6,68,69,70,71], 'try_chapter': True},
    'distraction': {'drop': [1,2,3,4,5,18]},
    'fade_to_black': {'drop': [45, 46]},
    'find_your_own_truth': {'drop': [1,2,3,4,40,41], 'try_chapter': True},
    'ghost_in_the_wires': {'drop': [1,2,3,4,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68]},
    'globalhead': {'drop': [1,2,3,4,18,19,20]},
    'headhunters': {'drop': [1,2,3,62,63,64], 'try_chapter': True},
    'heavens_river': {'drop': [1,2,3,4,5,6,7,8,78,79,80], 'try_chapter': True},
    'heavy_weather': {'drop': [1,2,3,4,15]},
    'holy_fire': {'drop': [1,2,3,4,11]},
    'house_of_the_sun': {'drop': [1,2,3,4,5,33], 'try_chapter': True},
    'i_robot': {'drop': [1,2,13,14,15]},
    'idoru': {'drop': [49,50,51,52]},
    'into_the_shadows': {'drop': [1,2,3,4,15,16,17,18], 'try_chapter': True},
    'islands_in_the_net': {'drop': [1,13,14,15,16], 'try_chapter': True},
    'johnny_mnemonic': {'try_chapter': True},
    'just_compensation': {'drop': [1,2,3,4,56,57], 'try_chapter': True},
    'lone_wolf': {'drop': [1]},
    'mirrorshades': {'drop': [14,15,16,17,18,19,20]},
    'never_deal_with_a_dragon': {'drop': [60,61]},
    'never_trust_an_elf': {'drop': [1,2,3,4,38,39], 'try_chapter': True},
    'nights_pawn': {'drop': [1], 'try_chapter': True},
    'nosferatu': {'drop': [1,2,3,34], 'try_chapter': True},
    'pattern_recognition': {'drop': [43], 'try_chapter': True},
    'preying_for_keeps': {'drop': [1,2,3,4,5,44,45], 'try_chapter': True},
    'reamde': {'drop': [1,2,3,4,5,28,29,30,31,32,33]},
    'schismatrix_plus': {'drop': [1,2,3,4]},
    'seveneves': {'drop': [1,2,3,4,23]},
    'shadowboxer': {'drop': [1,2,3,4,5,43,44], 'try_chapter': True},
    'shadowplay': {'drop': [1,2,3,4,43], 'try_chapter': True},
    'spook_country': {'drop': [1,2,3,4,5,6,7,8,93,94]},
    'steel_rain': {'drop': [1,2,3,45,46], 'try_chapter': True},
    'stranger_in_a_strange_land': {'drop': [1,2,3]},
    'stranger_souls': {'drop': [1,2,3,61,62], 'try_chapter': True},
    'streets_of_blood': {'drop': [1,2,3,38], 'try_chapter': True},
    'striper_assassin': {},
    'technobabel': {'drop': [1,2,3,4,5,37,38], 'try_chapter': True},
    'termination_shock': {'drop': [1,2,3,55], 'try_chapter': True},
    'the_art_of_deception': {'drop': [1,2,3,4,5,6,7,8,9,10,11,28,29,30,31], 'try_chapter': True},
    'the_demolished_man': {'drop': [1,2,3,4,5,6], 'try_chapter': True},
    'the_diamond_age': {'drop': [1,2,3,10,11,12,13]},
    'the_lucifer_deck': {'drop': [1,2,3,4,36,37]},
    'the_paradise_factory': {'drop': [1]},
    'the_peripheral': {'drop': [1,2,3,4,129,130], 'try_chapter': True},
    'the_stars_my_destination': {'drop': [1,2], 'try_chapter': True},
    'the_zenith_angle': {'drop': [1,2,3], 'try_chapter': True},
    'this_automatic_eden': {'drop': [1,69,70]},
    'virtual_light': {'drop': [1,2,3,4,44,45]},
    'we_are_legion': {'drop': [1,2,3,4]},
    'who_hunts_the_hunter': {'drop': [1,2,3,4,5,93,94], 'try_chapter': True},
    'wolf_raven': {'drop': [1]},
    'worlds_without_end': {'drop': [1,2,3,4,5,34,35,36,37]},
    'zero_history': {'drop': [1,2,90,91]},
}

all_books = pd.DataFrame([], columns=['book_name', 'paragraph_ix', 'chapter_ix', 'chapter_title', 'text', 'char_count', 'cumsum_char_count'])
for book in sorted(glob('source/*.epub')):
    name = os.path.splitext(os.path.basename(book))[0]
    print(f"Processing {name}")
    try_chapter = False
    clips = []
    drops = []
    if name in special:
        config = special[name]
        try_chapter = config.get('try_chapter', False)
        if 'clip' in config:
            clips = config['clip']
        if 'drop' in config:
            drops = config['drop']

    lines = parse_ebook_html(book, try_chapter=try_chapter)
    new_frame = pd.DataFrame(lines, columns=['book_name', 'paragraph_ix', 'chapter_ix', 'chapter_title', 'text', 'char_count', 'cumsum_char_count'])
    for drop in drops:
        new_frame = new_frame[new_frame['chapter_ix'] != drop]
    for clip in clips:
        # we want to remove the paragraph id's that are in the clip range, inclusive
        print(f"Clipping {clip}")
        idxr = range(clip[0], clip[1] + 1)
        new_frame = new_frame[~new_frame['paragraph_ix'].isin(idxr)]
            
    all_books = pd.concat([all_books, new_frame.copy()], ignore_index=True)
all_books.to_parquet('cyberpunk.parquet')
print(f"Saved {len(all_books)} paragraphs to cyberpunk.parquet")

Processing 1984
Processing 2xs


/mnt/biggy/ai/notebook/jupyterenv/lib/python3.10/site-packages/ebooklib/epub.py:1395: UserWarning: In the future version we will turn default option ignore_ncx to True.
  warnings.warn('In the future version we will turn default option ignore_ncx to True.')


Processing agency
Processing all_these_worlds
Processing all_tomorrows_parties
Processing allsystemsred
Processing alteredcarbon
Processing artificialcondition
Processing beyond_the_pale
Processing black_madonna
Processing blood_sport
Processing brave_new_world
Processing burning_bright
Processing burningchrome
Processing canticleforleibowitz
Processing changeling
Processing choose_your_enemies_carefully
Processing clockwork_asylum
Processing cryptonomicon
Clipping (1, 2)
Processing dead_air
Processing distraction
Processing exitstrategy
Processing fade_to_black
Processing find_your_own_truth
Processing forwearemany
Processing fugutuvetelemetry
Processing ghost_in_the_wires
Processing globalhead
Processing gnomon
Processing headhunters
Processing heavens_river
Processing heavy_weather
Processing holy_fire
Processing house_of_the_sun
Processing i_robot
Processing idoru
Processing into_the_shadows
Processing islands_in_the_net
Processing johnny_mnemonic
Processing just_compensation
Proce

/mnt/biggy/ai/notebook/jupyterenv/lib/python3.10/site-packages/ebooklib/epub.py:1395: UserWarning: In the future version we will turn default option ignore_ncx to True.
  warnings.warn('In the future version we will turn default option ignore_ncx to True.')


Processing the_lucifer_deck
Processing the_paradise_factory
Processing the_peripheral
Processing the_stars_my_destination
Processing the_zenith_angle
Processing theconfusion
Processing themoonisaharshmistress
Processing this_automatic_eden
Processing virtual_light
Processing we_are_legion
Processing who_hunts_the_hunter
Processing wolf_raven
Processing worlds_without_end
Processing zero_history
Saved 276984 paragraphs to cyberpunk.parquet
